# BASELINE evaluation on BIOMQM dataset

In [5]:
!git clone https://github.com/soniafoco/askqe_biomqm

Cloning into 'askqe_biomqm'...
remote: Enumerating objects: 146, done.
remote: Counting objects: 100% (146/146), done.
remote: Compressing objects: 100% (97/97), done.
remote: Total 146 (delta 73), reused 111 (delta 38), pack-reused 0 (from 0)
Receiving objects: 100% (146/146), 2.59 MiB | 3.47 MiB/s, done.
Resolving deltas: 100% (73/73), done.


In [6]:
%cd askqe_biomqm

/content/askqe_biomqm


In [7]:
!pip install -r requirements.txt

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.3/42.3 kB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 897.5/897.5 kB 17.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.8/100.8 kB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 4.9 MB/s eta 0:00:00


## Question generation
This script uses **Qwen2.5-3B-Instruct**, a 3B parameter instruction-tuned LLM, to generate questions from input sentences using bfloat16 inference.

For the BIOMQM evaluation, two distinct prompt versions can be run:
* **atomic** : uses the atomic facts extracted by the original authors, available in the repo, to generate more contextualized questions
* **vanilla**: generates questions direcly from the source

In [ ]:
!python QG/code/qwen-3b.py \
  --output_path vanilla_qwen-3b.jsonl \
  --prompt vanilla

tokenizer_config.json: 7.30kB [00:00, 28.1MB/s]
vocab.json: 2.78MB [00:00, 47.6MB/s]
merges.txt: 1.67MB [00:00, 129MB/s]
tokenizer.json: 7.03MB [00:00, 164MB/s]
config.json: 100%|█████████████████████████████| 661/661 [00:00<00:00, 4.04MB/s]
`torch_dtype` is deprecated! Use `dtype` instead!
2026-01-28 09:42:53.455453: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1769593373.844485     114 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1769593373.966238     114 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1769593374.968930     114 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking th

# Backtranslation
BIOMQM contains real translations from MT systems, with human annotations. Backtranslation is therefore performed on these translations using the **Google Translate** api.

In [ ]:
!python backtranslation.py \
  --input_path QG/vanilla_qwen-3b.jsonl \
  --output_path QG/vanilla_bt_qwen-3b.jsonl

Translation:  In diesem Fallbericht werden drei Fälle von zervikofazialem NF vorgestellt.
Backtranslation:  Three cases of cervicofacial NF are presented in this case report.
Translation:  Zwei der drei Patienten starben innerhalb von 48 h an einer systemischen Erkrankung mit septischem Organversagen; ein Patient wurde nach intensivmedizinischer Behandlung und Rekonstruktion der durch Debridement verursachten Gewebedefekte entlassen.
Backtranslation:  Two of the three patients died within 48 h of systemic disease with septic organ failure; one patient was discharged after intensive care treatment and reconstruction of the tissue defects caused by debridement.
Translation:  Ein schnelles Fortschreiten und eine systemische Erkrankung sind typisch für die Erkrankung und erschweren die Diagnose.
Backtranslation:  Rapid progression and systemic disease are typical of the disease and make diagnosis difficult.
Translation:  Nach der Diagnose von NF basierend auf klinischen Symptomen, Laborpar

## Question answering
This script uses **Qwen2.5-3B-Instruct**, a 3B parameter instruction-tuned LLM, to generate answers on the type of sentence given as input ("src" or "bt_tgt".


In [ ]:
!python QA/code/qwen-3b.py \
  --input_path QG/vanilla_qwen-3b.jsonl \
  --output_path QA/vanilla_src_qwen-3b.jsonl \
  --sentence_type src

`torch_dtype` is deprecated! Use `dtype` instead!
2026-01-29 07:53:53.897983: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1769673233.917069     190 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1769673233.922411     190 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1769673233.936250     190 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1769673233.936287     190 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1769673233.936292     190

In [ ]:
!python QA/code/qwen-3b.py \
  --input_path QG/vanilla_qwen-3b.jsonl \
  --output_path QA/vanilla_bt_qwen-3b.jsonl \
  --sentence_type bt_tgt

## Evaluation

In [ ]:
!python evaluation/sbert/sbert.py

In [ ]:
!python evaluation/string-comparison/string_comparison.py